# Step 1: Load the Dataset {.unnumbered}

In [1]:
import pandas as pd
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "vscode"
from pyspark.sql import SparkSession
from pyspark.sql.functions import split, explode, col, regexp_replace, transform, isnan


# Initialize Spark Session
spark = SparkSession.builder.appName("LightcastData").getOrCreate()

# Load Data
df = spark.read.option("header", "true").option("inferSchema", "true").option("multiLine","true").option("escape", "\"").csv("./data/lightcast_job_postings.csv")

# Show Schema and Sample Data
df.printSchema()
df.show(5)

your 131072x1 screen size is bogus. expect trouble
25/04/26 18:52:48 WARN Utils: Your hostname, DESKTOP-AEE21PF resolves to a loopback address: 127.0.1.1; using 192.168.167.208 instead (on interface eth0)
25/04/26 18:52:48 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/04/26 18:52:50 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


root
 |-- ID: string (nullable = true)
 |-- LAST_UPDATED_DATE: date (nullable = true)
 |-- LAST_UPDATED_TIMESTAMP: timestamp (nullable = true)
 |-- DUPLICATES: integer (nullable = true)
 |-- POSTED: date (nullable = true)
 |-- EXPIRED: date (nullable = true)
 |-- DURATION: integer (nullable = true)
 |-- SOURCE_TYPES: string (nullable = true)
 |-- SOURCES: string (nullable = true)
 |-- URL: string (nullable = true)
 |-- ACTIVE_URLS: string (nullable = true)
 |-- ACTIVE_SOURCES_INFO: string (nullable = true)
 |-- TITLE_RAW: string (nullable = true)
 |-- BODY: string (nullable = true)
 |-- MODELED_EXPIRED: date (nullable = true)
 |-- MODELED_DURATION: integer (nullable = true)
 |-- COMPANY: integer (nullable = true)
 |-- COMPANY_NAME: string (nullable = true)
 |-- COMPANY_RAW: string (nullable = true)
 |-- COMPANY_IS_STAFFING: boolean (nullable = true)
 |-- EDUCATION_LEVELS: string (nullable = true)
 |-- EDUCATION_LEVELS_NAME: string (nullable = true)
 |-- MIN_EDULEVELS: integer (nullable

25/04/26 18:52:56 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


+--------------------+-----------------+----------------------+----------+----------+----------+--------+--------------------+--------------------+--------------------+-----------+-------------------+--------------------+--------------------+---------------+----------------+--------+--------------------+-----------+-------------------+----------------+---------------------+-------------+-------------------+-------------+------------------+---------------+--------------------+--------------------+--------------------+-------------+------+-----------+----------------+-------------------+---------+-----------+--------------------+--------------------+-------------+------+--------------+-----+--------------------+-----+----------+---------------+--------------------+---------------+--------------------+------------+--------------------+------------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+---

In [3]:
columns = df.columns

# 对每一列应用 substr 函数，限制每列的输出为最多20个字符
df_truncated = df.limit(5)
for column in columns:
    df_truncated = df_truncated.withColumn(column, col(column).substr(1, 20))

df_truncated.limit(5).toPandas().head().to_html("data/lightcast_job_postings.html")

# Data Cleaning & Preprocessing

In [2]:
# 1.DURATION = EXPIRED - POSTED

spark.conf.set("spark.sql.legacy.timeParserPolicy", "LEGACY")

from pyspark.sql.functions import datediff, when, to_date, col

# 将日期列转换为日期格式
df = df.withColumn("POSTED", to_date("POSTED", "MM/dd/yyyy")) \
       .withColumn("EXPIRED", to_date("EXPIRED", "MM/dd/yyyy"))

# 直接用日期差填充 DURATION
df = df.withColumn(
    "DURATION",
    when(col("DURATION").isNull(), datediff("EXPIRED", "POSTED"))
    .otherwise(col("DURATION"))
)

df.select("POSTED", "EXPIRED", "DURATION").show(truncate=False)

+----------+----------+--------+
|POSTED    |EXPIRED   |DURATION|
+----------+----------+--------+
|2024-06-02|2024-06-08|6       |
|2024-06-02|2024-08-01|60      |
|2024-06-02|2024-07-07|35      |
|2024-06-02|2024-07-20|48      |
|2024-06-02|2024-06-17|15      |
|2024-06-02|2024-06-12|10      |
|2024-06-02|2024-08-01|60      |
|2024-06-02|2024-07-07|35      |
|2024-06-02|2024-06-20|18      |
|2024-06-02|2024-08-01|60      |
|2024-06-02|2024-09-27|117     |
|2024-06-02|2024-06-08|6       |
|2024-06-02|2024-07-05|33      |
|2024-06-02|2024-07-27|55      |
|2024-06-02|2024-08-01|60      |
|2024-06-02|2024-08-09|68      |
|2024-06-02|2024-06-20|18      |
|2024-06-02|2024-08-01|60      |
|2024-06-02|2024-08-01|60      |
|2024-06-02|2024-08-11|70      |
+----------+----------+--------+
only showing top 20 rows



In [3]:
# 2.SOURCE_TYPES, SOURCES, URL等列只保留双引号内容

from pyspark.sql.functions import regexp_replace, col

# 假设你已经有了DataFrame df，并且列名已经在 columns_to_clean 列表中
columns_to_clean = ["SOURCE_TYPES", "SOURCES", "URL", "EDUCATION_LEVELS_NAME", "SKILLS", 
                    "SKILLS_NAME", "SPECIALIZED_SKILLS", "SPECIALIZED_SKILLS_NAME", "CERTIFICATIONS", 
                    "CERTIFICATIONS_NAME", "COMMON_SKILLS", "COMMON_SKILLS_NAME", "SOFTWARE_SKILLS", 
                    "SOFTWARE_SKILLS_NAME", "CIP6", "CIP6_NAME", "CIP4", "CIP4_NAME", "CIP2", 
                    "CIP2_NAME", "LIGHTCAST_SECTORS", "LIGHTCAST_SECTORS_NAME"]  

# 批量处理每一列
for col_name in columns_to_clean:
    # 去除方括号、换行符、空格，并替换逗号之间的格式为", "，然后去掉双引号
    df = df.withColumn(col_name, 
                       regexp_replace(regexp_replace(regexp_replace(col(col_name), r'[\[\]\n\s]+', ''), r'","', '", '), r'"', ''))
    
df.show(10)

+--------------------+-------------------+----------------------+----------+----------+----------+--------+------------+--------------------+--------------------+-----------+-------------------+--------------------+--------------------+-------------------+----------------+---------+--------------------+--------------------+-------------------+----------------+---------------------+-------------+-------------------+-------------+------------------+---------------+--------------------+--------------------+--------------------+-------------+------+-----------+----------------+-------------------+---------+-----------+--------------------+--------------------+------------------+------+--------------------+-----+--------------------+-----+----------+---------------+--------------------+---------------+--------------------+------------+--------------------+------------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+------------

In [4]:
# 3.EDUCATION_LEVELS列只保留数字

from pyspark.sql.functions import regexp_extract

# 对 'EDUCATION_LEVELS' 列进行清理，只保留数字
df = df.withColumn("EDUCATION_LEVELS", regexp_extract("EDUCATION_LEVELS", r'(\d+)', 1))


df.select("EDUCATION_LEVELS").show(truncate=False)

+----------------+
|EDUCATION_LEVELS|
+----------------+
|2               |
|99              |
|2               |
|99              |
|99              |
|2               |
|2               |
|2               |
|99              |
|2               |
|0               |
|99              |
|2               |
|2               |
|99              |
|1               |
|1               |
|99              |
|2               |
|99              |
+----------------+
only showing top 20 rows



In [5]:
# 4.对LOCATION列进行处理

from pyspark.sql.functions import col, regexp_replace

# 去除大括号，并处理换行符和空格
df = df.withColumn("LOCATION", 
                           regexp_replace(regexp_replace(col("LOCATION"), r"\s*\n\s*", " "), r"[{}]", ""))


df.select("LOCATION").show(truncate=False)


+----------------------------------------+
|LOCATION                                |
+----------------------------------------+
| "lat": 33.20763, "lon": -92.6662674    |
| "lat": 44.3106241, "lon": -69.7794897  |
| "lat": 32.7766642, "lon": -96.7969879  |
| "lat": 33.4483771, "lon": -112.0740373 |
| "lat": 37.6392595, "lon": -120.9970014 |
| "lat": 0, "lon": 0                     |
| "lat": 33.4941704, "lon": -111.9260519 |
| "lat": 39.7589478, "lon": -84.1916069  |
| "lat": 41.1220409, "lon": -74.5804378  |
| "lat": 40.7501, "lon": -73.997         |
| "lat": 35.6224561, "lon": -117.6708966 |
| "lat": 21.3069444, "lon": -157.8583333 |
| "lat": 0, "lon": 0                     |
| "lat": 42.331427, "lon": -83.0457538   |
| "lat": 32.2987573, "lon": -90.1848103  |
| "lat": 42.3600825, "lon": -71.0588801  |
| "lat": 0, "lon": 0                     |
| "lat": 58.3019444, "lon": -134.4197221 |
| "lat": 33.5185892, "lon": -86.8103567  |
| "lat": 37.7749295, "lon": -122.4194155 |
+----------

In [6]:
# 5.MODELED_DURATION = MODELED_EXPIRED - POSTED

spark.conf.set("spark.sql.legacy.timeParserPolicy", "LEGACY")

from pyspark.sql.functions import datediff, when, to_date, col

# 将日期列转换为日期格式
df = df.withColumn("MODELED_EXPIRED", to_date("MODELED_EXPIRED", "MM/dd/yyyy"))

# 直接用日期差填充 DURATION
df = df.withColumn(
    "MODELED_DURATION",
    when(col("MODELED_DURATION").isNull(), datediff("MODELED_EXPIRED", "POSTED"))
    .otherwise(col("MODELED_DURATION"))
)

df.select("POSTED", "MODELED_EXPIRED", "MODELED_DURATION").show(truncate=False)

+----------+---------------+----------------+
|POSTED    |MODELED_EXPIRED|MODELED_DURATION|
+----------+---------------+----------------+
|2024-06-02|2024-06-08     |6               |
|2024-06-02|2024-08-01     |60              |
|2024-06-02|2024-06-10     |8               |
|2024-06-02|2024-06-12     |10              |
|2024-06-02|2024-06-17     |15              |
|2024-06-02|2024-06-12     |10              |
|2024-06-02|2024-06-22     |20              |
|2024-06-02|2024-06-10     |8               |
|2024-06-02|2024-06-20     |18              |
|2024-06-02|2024-08-01     |60              |
|2024-06-02|2024-07-13     |41              |
|2024-06-02|2024-06-08     |6               |
|2024-06-02|2024-07-05     |33              |
|2024-06-02|2024-07-27     |55              |
|2024-06-02|2024-06-14     |12              |
|2024-06-02|2024-06-08     |6               |
|2024-06-02|2024-06-20     |18              |
|2024-06-02|2024-07-10     |38              |
|2024-06-02|2024-08-01     |60    

In [3]:
# 6. Standardize Remote Work Types
from pyspark.sql.functions import when, col

df = df.withColumn(
    "REMOTE_TYPE_NAME",
    when(col("REMOTE_TYPE_NAME") == "[None]", "On-Site")
    .when(col("REMOTE_TYPE_NAME").isNull(), "On-Site")
    .when(col("REMOTE_TYPE_NAME") == "Not Remote", "On-Site")
    .when(col("REMOTE_TYPE_NAME") == "Hybrid Remote", "Hybrid")
    .when(col("REMOTE_TYPE_NAME") == "Remote", "Remote")
    .otherwise(col("REMOTE_TYPE_NAME"))  # 保持其他不变
)

df.select("REMOTE_TYPE_NAME").distinct().show(truncate=False)

+----------------+
|REMOTE_TYPE_NAME|
+----------------+
|Remote          |
|Hybrid          |
|On-Site         |
+----------------+



In [8]:
# 保存数据：
# 1. 使用 coalesce(1) 将所有分区的数据合并为一个文件
df.coalesce(1).write.option("header", "true").csv("data/lightcast_cleaned_temp")

# 2. 查找生成的文件并重命名
import os
import shutil

# 获取生成的文件路径
generated_file_path = 'data/lightcast_cleaned_temp'

# 获取文件夹中的所有文件（应只有一个文件）
for filename in os.listdir(generated_file_path):
    if filename.startswith('part-'):  # 找到 part 文件
        # 重命名并移动到目标位置
        shutil.move(os.path.join(generated_file_path, filename), 'data/lightcast_cleaned.csv')

# 删除临时文件夹
shutil.rmtree(generated_file_path)


# Load New Dataset

In [4]:
import pandas as pd
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "vscode"
from pyspark.sql import SparkSession
from pyspark.sql.functions import split, explode, col, regexp_replace, transform, isnan

spark = SparkSession.builder.appName("LightcastCleanedData").getOrCreate()

# 重新加载处理后的数据
df_cleaned = spark.read.option("header", "true").option("inferSchema", "true").option("multiLine","true").csv("data/lightcast_cleaned.csv")

# 查看数据结构和样本
df_cleaned.show(5)

25/04/26 19:00:16 WARN SparkSession: Using an existing Spark session; only runtime SQL configurations will take effect.


+--------------------+-------------------+----------------------+----------+----------+----------+--------+------------+--------------------+--------------------+-----------+-------------------+--------------------+--------------------+---------------+----------------+--------+--------------------+-----------+-------------------+----------------+---------------------+-------------+-------------------+-------------+------------------+---------------+--------------------+--------------------+--------------------+-------------+------+-----------+----------------+-------------------+---------+-----------+--------------------+--------------------+-------------+------+--------------+-----+--------------------+-----+----------+---------------+--------------------+---------------+--------------------+------------+--------------------+------------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+---------

In [5]:
columns_cleaned = df_cleaned.columns

# 对每一列应用 substr 函数，限制每列的输出为最多20个字符
df_cleaned_truncated = df.limit(5)
for column in columns:
    df_cleaned_truncated = df_cleaned_truncated.withColumn(column, col(column).substr(1, 20))

df_cleaned_truncated.limit(5).toPandas().head().to_html("data/lightcast_cleaned.html")


# Exploratory Data Analysis (EDA)

## 1. Comparison of salary between remote and on-site work (box chart)

In [2]:
import pandas as pd
import plotly.express as px
# 使用 .collect() 收集数据
data = df_cleaned.select("REMOTE_TYPE_NAME", "SALARY").collect()

# 将数据转换为适合绘图的格式（如列表）
data_list = [(row["REMOTE_TYPE_NAME"], row["SALARY"]) for row in data]

# 创建一个 Pandas DataFrame
import pandas as pd
df_pandas = pd.DataFrame(data_list, columns=["REMOTE_TYPE_NAME", "SALARY"])

fig = px.box(df_pandas, x="REMOTE_TYPE_NAME", y="SALARY",
             title="Salary Comparison: Remote vs. On-Site Jobs",
             category_orders={"REMOTE_TYPE_NAME": ["On-Site", "Hybrid", "Remote"]},
             labels={"REMOTE_TYPE_NAME": "Job Type", "SALARY": "Salary ($)"})

fig.write_html("./images/REMOTE_TYPE_NAME&SALARY.html")
fig.write_image("./images/REMOTE_TYPE_NAME&SALARY.png")

fig.show()

## 2. Salary by region (map)

In [3]:
#STATE_NAME改为简写
import us

# 使用 .collect() 收集数据
data = df_cleaned.select("STATE_NAME", "SALARY").collect()

# 将数据转换为适合绘图的格式（如列表）
data_list = [(row["STATE_NAME"], row["SALARY"]) for row in data]

# 创建一个 Pandas DataFrame
import pandas as pd
df_pandas = pd.DataFrame(data_list, columns=["STATE_NAME", "SALARY"])

df_pandas["STATE_NAME"] = df_pandas["STATE_NAME"].apply(
    lambda x: us.states.lookup(x).abbr if pd.notna(x) and us.states.lookup(x) else x
)

df_pandas[["STATE_NAME", "SALARY"]]

STATE_NAME    SALARY
0             AR       NaN
1             ME       NaN
2             TX       NaN
3             AZ       NaN
4             CA   92500.0
...          ...       ...
72471         VA       NaN
72472         MA  169275.0
72473         MI   72800.0
72474         ME       NaN
72475         TX       NaN

[72476 rows x 2 columns]

In [4]:
#Verify conversion

import plotly.express as px

fig = px.choropleth(df_pandas, 
                    locations="STATE_NAME", 
                    locationmode="USA-states",
                    color="SALARY", 
                    hover_name="STATE_NAME",
                    scope="usa", 
                    title="Average Salary by State",
                    color_continuous_scale="Viridis",
                    labels={"SALARY": "Average Salary ($)"})

fig.write_image("./images/STATE_NAME&SALARY.png")
fig.write_html("./images/STATE_NAME_SALARY.html")

fig.show()


## 3. The highest paying job

In [5]:
# 使用 .collect() 收集数据
data = df_cleaned.select("LIGHTCAST_SECTORS_NAME", "SALARY").collect()

# 将数据转换为适合绘图的格式（如列表）
data_list = [(row["LIGHTCAST_SECTORS_NAME"], row["SALARY"]) for row in data]

# 创建一个 Pandas DataFrame
import pandas as pd
df_pandas = pd.DataFrame(data_list, columns=["LIGHTCAST_SECTORS_NAME", "SALARY"])

df_pandas[["LIGHTCAST_SECTORS_NAME", "SALARY"]]

LIGHTCAST_SECTORS_NAME    SALARY
0      ArtificialIntelligence       NaN
1                        None       NaN
2                        None       NaN
3      DataPrivacy/Protection       NaN
4                        None   92500.0
...                       ...       ...
72471  ArtificialIntelligence       NaN
72472           Cybersecurity  169275.0
72473                    None   72800.0
72474                    None       NaN
72475                    None       NaN

[72476 rows x 2 columns]

In [6]:

fig = px.bar(df_pandas.groupby("LIGHTCAST_SECTORS_NAME")["SALARY"].mean().sort_values(ascending=False).head(10),
             title="Top 10 Industries with Highest Salaries",
             labels={"LIGHTCAST_SECTORS_NAME": "Industry", "SALARY": "Salary ($)"})

fig.write_html("./images/LIGHTCAST_SECTORS_NAME&SALARY.html")
fig.write_image("./images/LIGHTCAST_SECTORS_NAME&SALARY.png")

fig.show()

## 4. Salary comparison between AI and non-AI positions

In [10]:
#Define AI-related keywords based on LIGHTCAST_SECTORS_NAME
ai_keywords = [
    "Artificial Intelligence", "Machine Learning", "Data Science",
    "Cybersecurity", "Computational Science", "Deep Learning",
    "Data Privacy", "Computer Vision", "Natural Language Processing",
    "Big Data", "Cloud Computing", "Quantum Computing", "Robotics"
]

# 使用 .collect() 收集数据
data = df_cleaned.select("LIGHTCAST_SECTORS_NAME", "SALARY").collect()

# 将数据转换为适合绘图的格式（如列表）
data_list = [(row["LIGHTCAST_SECTORS_NAME"], row["SALARY"]) for row in data]

# 创建一个 Pandas DataFrame
import pandas as pd
df_pandas = pd.DataFrame(data_list, columns=["LIGHTCAST_SECTORS_NAME", "SALARY"])

df_pandas[["LIGHTCAST_SECTORS_NAME", "SALARY"]]

LIGHTCAST_SECTORS_NAME    SALARY
0      ArtificialIntelligence       NaN
1                        None       NaN
2                        None       NaN
3      DataPrivacy/Protection       NaN
4                        None   92500.0
...                       ...       ...
72471  ArtificialIntelligence       NaN
72472           Cybersecurity  169275.0
72473                    None   72800.0
72474                    None       NaN
72475                    None       NaN

[72476 rows x 2 columns]

In [11]:
#Classify AI-related vs. Non-AI industries
df_pandas["AI_RELATED"] = df_pandas["LIGHTCAST_SECTORS_NAME"].apply(
    lambda x: "AI-related" if any(keyword in str(x) for keyword in ai_keywords) else "Non-AI"
)

# Show counts of AI vs. Non-AI jobs
print(df_pandas["AI_RELATED"].value_counts())

AI_RELATED
Non-AI        68195
AI-related     4281
Name: count, dtype: int64


In [12]:
import plotly.express as px

fig = px.box(df_pandas, x="AI_RELATED", y="SALARY",
             title="AI-related vs. Non-AI Industries Salary Comparison",
             labels={"AI_RELATED": "Industry Type", "SALARY": "Salary ($)"},
             color="AI_RELATED")

fig.write_html("./images/AI_RELATED&SALARY.html")

fig.show()